<a href="https://colab.research.google.com/github/monicamons12/30DayMapChallenge/blob/Monica/OSM_Extraction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
# Install GDAL and Geopandas
!apt install gdal-bin python-gdal python3-gdal --quiet
!apt install python3-rtree --quiet
!pip install git+git://github.com/geopandas/geopandas.git --quiet
!pip install descartes --quiet
!pip install osmnx==1.1.1
!pip install folium

Reading package lists...
Building dependency tree...
Reading state information...
gdal-bin is already the newest version (2.2.3+dfsg-2).
python-gdal is already the newest version (2.2.3+dfsg-2).
The following additional packages will be installed:
  python3-numpy
Suggested packages:
  python-numpy-doc python3-nose python3-numpy-dbg
The following NEW packages will be installed:
  python3-gdal python3-numpy
0 upgraded, 2 newly installed, 0 to remove and 39 not upgraded.
Need to get 2,288 kB of archives.
After this operation, 13.2 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu bionic/main amd64 python3-numpy amd64 1:1.13.3-2ubuntu1 [1,943 kB]
Get:2 http://archive.ubuntu.com/ubuntu bionic/universe amd64 python3-gdal amd64 2.2.3+dfsg-2 [346 kB]
Fetched 2,288 kB in 1s (2,165 kB/s)
Selecting previously unselected package python3-numpy.
(Reading database ... 160815 files and directories currently installed.)
Preparing to unpack .../python3-numpy_1%3a1.13.3-2ub

In [13]:
import pandas as pd
import geopandas as gpd
import osmnx
import folium
from folium.plugins import MousePosition
import matplotlib.pyplot as plt
import seaborn as sb

#Add Folium Map with plugins, Extract Features from OSM and Calculate Routes from OSM network

*   Folium helps to add manipulated python data to Leaflet Map for visualization
*   It has in-built visualisation capabilities, added up by plugins (Draw, MiniMap, Geolocator, etc.,.)





In [4]:
map = folium.Map([13.1031, 80.1794], zoom_start=10, tiles="CartoDb dark_matter")
map.add_child(folium.ClickForMarker())
MousePosition().add_to(map)
from folium.plugins import MiniMap
MiniMap(tile_layer='Stamen WaterColor', position='bottomleft').add_to(map)
map

## Extracting Street Map from OSM
It is possible to extract networks from OSM using OSMNX package. 
Various ways to extract - by specifying city, by the input of bbox, from point/address.

network_type can be 'drive' or 'walk' or 'bike'

save_graph_geopackage can also be used to save the network graph as geopackage instead of shapefile as mentioned in the following code

In [5]:
place = "Chennai, India"
graph = osmnx.graph.graph_from_place(place, network_type='drive')
#osmnx.io.save_graph_shapefile(graph)

In [6]:
len(graph)

58921

In [7]:
nodes, streets = osmnx.graph_to_gdfs(graph)

In [8]:
nodes.head()

y          x  ... street_count                   geometry
osmid                           ...                                        
30037235  13.080784  80.265167  ...            4  POINT (80.26517 13.08078)
30037236  13.080295  80.262785  ...            4  POINT (80.26278 13.08030)
30037239  13.079431  80.258773  ...            4  POINT (80.25877 13.07943)
30037240  13.079196  80.256659  ...            4  POINT (80.25666 13.07920)
30037241  13.078997  80.254681  ...            4  POINT (80.25468 13.07900)

[5 rows x 5 columns]

In [9]:
streets.head()

osmid  oneway  ... service est_width
u        v          key                     ...                  
30037235 2197652486 0    209562047    True  ...     NaN       NaN
         254497449  0    237621838    True  ...     NaN       NaN
30037236 304918752  0     27768980   False  ...     NaN       NaN
         254497666  0    237621838    True  ...     NaN       NaN
         2486635736 0     27768980   False  ...     NaN       NaN

[5 rows x 16 columns]

In [10]:
street_types = pd.DataFrame(streets["highway"].apply(pd.Series)[0].value_counts().reset_index())
street_types.columns = ["type", "count"]

In [ ]:
fig, ax = plt.subplots(figsize=(12,10))
sb.stripplot(y="type", x="count", data=street_types, ax=ax)
plt.tight_layout()
plt.savefig("stripplot.png")
#sb.barplot(y="type", x="count", data=street_types, ax=ax)
#plt.tight_layout()
#plt.savefig("barchart.png")

In [16]:

style = {'color': '#F7DC6F', 'weight':'1'}
m = folium.Map([13.1031, 80.1794],zoom_start=15,tiles="CartoDb positron")
streetsJson = folium.GeoJson(streets, style_function=lambda x: style).add_to(m)
folium.GeoJsonTooltip(fields=['name'])
m.save("streets.html")
m

## Extract buildings from OSM

In [17]:
buildings = osmnx.geometries.geometries_from_place(place, {'building': True})

In [18]:
buildings.head()

is_in  ... townhall:type
element_type osmid                  ...              
node         330774732  IIT Madras  ...           NaN
             330774733  IIT Madras  ...           NaN
             330774734  IIT Madras  ...           NaN
             330774735  IIT Madras  ...           NaN
             330774737  IIT Madras  ...           NaN

[5 rows x 189 columns]

In [19]:
buildings.shape

(256563, 189)

In [20]:
cols = ['amenity','building', 'name', 'tourism']
buildings[cols].head()

amenity  ... tourism
element_type osmid              ...        
node         330774732     NaN  ...     NaN
             330774733     NaN  ...     NaN
             330774734     NaN  ...     NaN
             330774735     NaN  ...     NaN
             330774737     NaN  ...     NaN

[5 rows x 4 columns]

In [21]:
list(buildings.columns)

['is_in',
 'name',
 'name:en',
 'name:hi',
 'name:ta',
 'wikidata',
 'wikipedia',
 'geometry',
 'created_by',
 'addr:postcode',
 'addr:street',
 'building',
 'building:levels',
 'addr:city',
 'alt_name',
 'amenity',
 'brand:wikidata',
 'cuisine',
 'diet:vegetarian',
 'email',
 'food',
 'operator',
 'phone',
 'smoking',
 'website',
 'landuse',
 'office',
 'shop',
 'addr:housenumber',
 'int_name',
 'old_name',
 'addr:housename',
 'leisure',
 'designation',
 'source',
 'description',
 'tourism',
 'bus',
 'highway',
 'public_transport',
 'ele',
 'opening_hours',
 'recycling:batteries',
 'recycling:books',
 'recycling:cardboard',
 'recycling:electrical_appliances',
 'recycling:glass',
 'recycling:glass_bottles',
 'recycling:magazines',
 'recycling:newspaper',
 'recycling:paper',
 'recycling:plastic_packaging',
 'recycling_type',
 'access',
 'barrier',
 'comment',
 'religion',
 'entrance',
 'atm',
 'brand',
 'brand:wikipedia',
 'short_name',
 'denomination',
 'admin_level',
 'internet_access

In [22]:
buildings["amenity"].apply(pd.Series)[0].value_counts()


place_of_worship    130
restaurant           52
bank                 17
hospital             15
bus_station          13
school               12
cafe                 11
cinema               10
community_centre      8
library               7
events_venue          5
public_building       4
marketplace           4
college               3
theatre               3
post_office           3
food_court            3
police                3
townhall              3
dojo                  3
pharmacy              3
parking               3
auditorium            2
fast_food             2
fuel                  2
shelter               2
driving_school        2
toilets               2
studio                1
arts_centre           1
university            1
ice_cream             1
apartment             1
crematorium           1
community_hall        1
recycling             1
social_facility       1
courthouse            1
clinic                1
Name: 0, dtype: int64

In [23]:

style_buildings = {'color':'#6C3483 ', 'fillColor': '#6C3483 ', 'weight':'1', 'fillOpacity' : 1}

m = folium.Map([13.1031, 80.1794],
               zoom_start=15,
               tiles="cartoDb positron")

buildingJson = folium.GeoJson(buildings[:1000], style_function=lambda x: style_buildings).add_to(m)
folium.GeoJsonTooltip(fields=['name','amenity'], labels=False).add_to(buildingJson)
m.save("buildings.html")
m

## Hospitals in Chennai

In [24]:
hospitals = osmnx.geometries.geometries_from_place(place, {'amenity':'hospital'})

In [25]:
hospitals.head()

amenity healthcare  ... contact:email amenity_1
element_type osmid                           ...                        
node         248420920  hospital   hospital  ...           NaN       NaN
             258978416  hospital        NaN  ...           NaN       NaN
             258978417  hospital        NaN  ...           NaN       NaN
             262452334  hospital        NaN  ...           NaN       NaN
             289486820  hospital        NaN  ...           NaN       NaN

[5 rows x 47 columns]

In [26]:
hospitals.shape

(619, 47)

In [27]:
hospitals.columns

Index(['amenity', 'healthcare', 'healthcare:speciality', 'is_in', 'name',
       'name:en', 'name:ta', 'operator', 'wikidata', 'geometry',
       'addr:district', 'addr:full', 'addr:postcode', 'addr:state',
       'operator:type', 'source', 'website', 'addr:subdistrict', 'email',
       'addr:block', 'addr:city', 'created_by', 'wikipedia', 'addr:street',
       'phone', 'wheelchair', 'opening_hours', 'addr:housenumber', 'emergency',
       'designation', 'addr:interpolation', 'addr:housename', 'note',
       'description', 'internet_access', 'nodes', 'contact:mobile',
       'contact:phone', 'name:hi', 'building', 'addr:suburb', 'alt_name',
       'fax', 'building:levels', 'comment', 'contact:email', 'amenity_1'],
      dtype='object')

In [28]:
columns =['name','name:en', 'healthcare', 'healthcare:speciality', 'opening_hours', 'operator:type', 'addr:street', 'addr:city','addr:postcode', 'contact:phone']
hospitals[columns].head()

name  ... contact:phone
element_type osmid                                    ...              
node         248420920   Kalaignar Karunanidhi Nagar  ...           NaN
             258978416                Amrit Hospital  ...           NaN
             258978417               Vikram Hospital  ...           NaN
             262452334          City Tower Hospitals  ...           NaN
             289486820  Apollo Hospitals, Tondiarpet  ...           NaN

[5 rows x 10 columns]

In [29]:
hospital_points = hospitals[hospitals.geom_type == "Point"]

In [30]:
m = folium.Map([13.1031, 80.1794], zoom_start=10, tiles="CartoDb dark_matter")
locs = zip(hospital_points.geometry.y, hospital_points.geometry.x)
for location in locs:
    folium.CircleMarker(location=location, popup=folium.Popup(location) , color = "#F4F6F6",   radius=2).add_to(m)
m.save("hospitals.html")
m

##Calculate Shortest Path using OSMNX and Plot Route



In [31]:
dist_array = osmnx.distance.shortest_path(graph, 30037235, 30037241 )
route = osmnx.plot.plot_graph_route(graph, dist_array, route_color='r')

ImportError: ignored

<Figure size 576x576 with 1 Axes>